# Reducing the energy spread in our X-band linac

In [ ]:
%plot -f SVG

In [ ]:
RF_Track;

## Load the lattice from appropriate scripts

In [ ]:
addpath('scripts/')

## Let's define some key parameters
We use a structure to collect all relevant parameters

In [ ]:
%% Structure "setup"
setup.Q = -1; % single-particle charge, in units of e
setup.mass = RF_Track.electronmass; % MeV/c^2
setup.population = RF_Track.nC; % 50 * RF_Track.pC; % number of real particles per bunch

setup.sigma_t = 0.100; % mm/c
setup.sigma_pt = 0.1; % permil, momentum spread

setup.P_i = 100; % initial momentum, MeV/c
setup.P_f = 500; % final momentum, MeV/c

setup.phid = 0; % deg, phase of the RF structures
setup.mu = 90; % deg, FODO phase advance per cell

## Let's build the linac lattice
We use a standard FODO lattice, with four structures every two consecutive quadrupoles and 90 degrees phase advance per cell

In [ ]:
LINAC = init_linac_lattice (setup);

In [ ]:
LINAC.size()

In [ ]:
LINAC.get_length()

## Let's define and track the reference particle

In [ ]:
P0 = init_reference_particle (setup);

% Track the reference particle
P1 = LINAC.track(P0);

In [ ]:
P1.get_phase_space()

## ...and a bunch

In [ ]:
B0 = init_bunch(setup);

## Perform tracking

In [ ]:
B1 = LINAC.track(B0);

Let's make some plots...

In [ ]:
M0 = B0.get_phase_space ('%x %xp %y %yp %dt %P');
M1 = B1.get_phase_space ('%x %xp %y %yp %dt %P');

figure
hold on
scatter(M0(:,1), M0(:,2))
scatter(M1(:,1), M1(:,2))
legend({'initial', 'final'});
xlabel('x [mm]');
ylabel('x'' [mrad]');

figure
hold on
scatter(M0(:,3), M0(:,4))
scatter(M1(:,3), M1(:,4))
legend({'initial', 'final'});
xlabel('y [mm]');
ylabel('y'' [mrad]');

figure
scatter(M1(:,5), M1(:,6))
xlabel('dt [mm/c]');
ylabel('P [MeV/c]');

In [ ]:
T = LINAC.get_transport_table('%S %mean_x %mean_y');

hold on
plot(T(:,1), T(:,2), 'b-', 'linewidth', 2);
plot(T(:,1), T(:,3), 'r-', 'linewidth', 2);
legend('X', 'Y');
xlabel('S [m]');
ylabel('position [mm]');

In [ ]:
T = LINAC.get_transport_table('%S %emitt_x %emitt_y');

hold on
plot(T(:,1), T(:,2), 'b-', 'linewidth', 2);
plot(T(:,1), T(:,3), 'r-', 'linewidth', 2);
legend('emitt_x', 'emitt_y');
xlabel('S [m]');
ylabel('norm. emitt [mm.mrad]');

## Intermezzo
### Fitting the transfer matrix

In [ ]:
% Transfer matrix of the linac
M0 = B0.get_phase_space('%x %xp %y %yp %dt %pt');
M1 = B1.get_phase_space('%x %xp %y %yp %dt %pt');

x0  = M0(:,1);
xp0 = M0(:,2);
y0  = M0(:,3);
yp0 = M0(:,4);
t0  = M0(:,5);
d0  = M0(:,6);

x1  = M1(:,1);
xp1 = M1(:,2);
y1  = M1(:,3);
yp1 = M1(:,4);
t1  = M1(:,5);
d1  = M1(:,6);

I = ones (size(x0));
I1 = [ x1 xp1 y1 yp1 t1 d1 ];
I0 = [ I ... % K - 0th order
       x0 xp0 y0 yp0 t0 d0 ]; % R - 1st order

M = (I1') / (I0');
K = M(:,1)
R = M(:,2:7)

% Tracking
I1 = ([ K R ] * I0')';

Let's include higher orders

In [ ]:
% Transfer matrix of the linac
M0 = B0.get_phase_space('%x %xp %y %yp %dt %pt');
M1 = B1.get_phase_space('%x %xp %y %yp %dt %pt');

x0  = M0(:,1);
xp0 = M0(:,2);
y0  = M0(:,3);
yp0 = M0(:,4);
t0  = M0(:,5);
d0  = M0(:,6);

x1  = M1(:,1);
xp1 = M1(:,2);
y1  = M1(:,3);
yp1 = M1(:,4);
t1  = M1(:,5);
d1  = M1(:,6);

I = ones (size(x0));
I1 = [ x1 xp1 y1 yp1 t1 d1 ];
I0 = [ I ... % K - 0th order
       x0 xp0 y0 yp0 t0 d0 ... % R - 1st order
       x0.^2 xp0.^2 y0.^2 yp0.^2 t0.^2 d0.^2 ... % T 2nd-order
       x0.*xp0 x0.*y0 x0.*yp0 x0.*t0 x0.*d0 ...  % T
       xp0.*y0 xp0.*yp0 xp0.*t0 xp0.*d0 ... % T
       y0.*yp0 y0.*t0 y0.*d0 ... % T
       yp0.*t0 yp0.*d0 ... % T
       t0.*d0 ... % T
       d0.*d0.*d0 d0.*d0.*t0 d0.*d0.*x0 d0.*d0.*xp0 d0.*d0.*y0 ... % U - 3rd order
       d0.*d0.*yp0 d0.*t0.*t0 d0.*t0.*x0 d0.*t0.*xp0 d0.*t0.*y0 ... % U
       d0.*t0.*yp0 d0.*x0.*x0 d0.*x0.*xp0 d0.*x0.*y0 d0.*x0.*yp0 ... % U
       d0.*xp0.*xp0 d0.*xp0.*y0 d0.*xp0.*yp0 d0.*y0.*y0 ... % U
       d0.*y0.*yp0 d0.*yp0.*yp0 t0.*t0.*t0 t0.*t0.*x0 t0.*t0.*xp0 ... % U
       t0.*t0.*y0 t0.*t0.*yp0 t0.*x0.*x0 t0.*x0.*xp0 t0.*x0.*y0 ... % U
       t0.*x0.*yp0 t0.*xp0.*xp0 t0.*xp0.*y0 t0.*xp0.*yp0 ... % U
       t0.*y0.*y0 t0.*y0.*yp0 t0.*yp0.*yp0 x0.*x0.*x0 x0.*x0.*xp0 ... % U
       x0.*x0.*y0 x0.*x0.*yp0 x0.*xp0.*xp0 x0.*xp0.*y0 ... % U
       x0.*xp0.*yp0 x0.*y0.*y0 x0.*y0.*yp0 x0.*yp0.*yp0 ... % U
       xp0.*xp0.*xp0 xp0.*xp0.*y0 xp0.*xp0.*yp0 xp0.*y0.*y0 ... % U
       xp0.*y0.*yp0 xp0.*yp0.*yp0 y0.*y0.*y0 y0.*y0.*yp0 ... % U
       y0.*yp0.*yp0 yp0.*yp0.*yp0 ]; % U

M = (I1') / (I0');
K = M(:,1)
R = M(:,2:7)
T = M(:,8:28);
U = M(:,29:end);

% Tracking
I1 = ([ K R T U ] * I0')';

In [ ]:
K
R
T

## Let's reduce the energy spread

Perform a 1D optimisation of the phase

In [ ]:
function M = merit (LINAC, B0, phid)
    RF_Track;
    
    % set the phase of all structures
    for rf = LINAC.get_rf_elements()
        rf{1}.set_phid(phid);
    end
    
    % perform tracking
    B1 = LINAC.track(B0);
    I1 = B1.get_info();

    % M1 = B1.get_phase_space();
    % M = std(M1(:,6));
    
    % return the momentum spread
    M = I1.sigma_pt;

    % display some numbers...
    disp([ phid M ]);
end

phid_min = fminbnd ( @(PHID) merit(LINAC, B0, PHID), -30, 30)

Update the linac lattice to use the new phase

In [ ]:
setup.phid = phid_min;

LINAC_1 = init_linac_lattice(setup); % recreate the linac

In [ ]:
B1 = LINAC_1.track(B0);

In [ ]:
T = LINAC_1.get_transport_table('%S %emitt_x %emitt_y');

hold on
plot(T(:,1), T(:,2), 'b-', 'linewidth', 2);
plot(T(:,1), T(:,3), 'r-', 'linewidth', 2);
legend('emitt_x', 'emitt_y');
xlabel('S [m]');
ylabel('norm. emitt [mm.mrad]');

In [ ]:
M0 = B0.get_phase_space ('%x %xp %y %yp %dt %d');
M1 = B1.get_phase_space ('%x %xp %y %yp %dt %d');

figure
hold on
scatter(M0(:,1), M0(:,2))
scatter(M1(:,1), M1(:,2))
legend({'initial', 'final'});
xlabel('x [mm]');
ylabel('x'' [mrad]');

figure
hold on
scatter(M0(:,3), M0(:,4))
scatter(M1(:,3), M1(:,4))
legend({'initial', 'final'});
xlabel('y [mm]');
ylabel('y'' [mrad]');

figure
hold on
scatter(M0(:,5), M0(:,6))
scatter(M1(:,5), M1(:,6))
legend({'initial', 'final'});
xlabel('dt [mm/c]');
ylabel('P [MeV/c]');